In [ ]:
# Working with Gridded Data I 

In [ ]:
import iris
import numpy as np
import xarray as xr
import holoviews as hv
import geoviews as gv
import geoviews.feature as gf
from cartopy import crs

#hv.notebook_extension()
hv.extension('matplotlib', 'bokeh')

In [ ]:
#http://geo.holoviews.org/Gridded_Datasets_I.html

#conda install -c conda-forge iris
#conda install -c conda-forge iris-sample-data
#conda install -c conda-forge -c ioam holoviews geoviews

In [ ]:
%opts Image {+framewise} [colorbar=True] Curve [xrotation=60]

In [ ]:
%output max_frames=1000 

In [ ]:
%%opts Feature [projection=crs.Geostationary()]
(gf.ocean + gf.land + gf.ocean * gf.land * gf.coastline * gf.borders).cols(3)

In [ ]:
xr.open_dataset('./sample-data/pre-industrial.nc').longitude

In [ ]:
%%opts Image [colorbar=True fig_size=200] (cmap='viridis')
ensemble = xr.open_dataset('./sample-data/ensemble.nc')
dataset = gv.Dataset(ensemble, kdims=['longitude', 'latitude', 'time'], crs=crs.PlateCarree())
dataset.to(gv.Image, ['longitude', 'latitude'], ['surface_temperature'], ['time']) * gf.coastline()

In [ ]:
xr_ensemble = xr.open_dataset('./sample-data/ensemble.nc')
kdims = ['time', 'longitude', 'latitude']
vdims = ['surface_temperature']

xr_dataset = gv.Dataset(xr_ensemble, kdims=kdims, vdims=vdims, crs=crs.PlateCarree())
hv.Dimension.type_formatters[np.datetime64] = '%Y-%m-%d'

xr_dataset.to(gv.Image, ['longitude', 'latitude'])

In [ ]:
air_temperature = gv.Dataset(xr.open_dataset('./sample-data/pre-industrial.nc'), kdims=['longitude', 'latitude'],
                             group='Pre-industrial air temperature', vdims=['air_temperature'],
                             crs=crs.PlateCarree())

(xr_dataset.to.image(['longitude', 'latitude'])+
 air_temperature.to.image(['longitude', 'latitude']))

In [ ]:
%%opts Curve [aspect=2 xticks=4 xrotation=15] Points (color='k')
temp_curve = hv.Curve(xr_dataset.select(longitude=300, latitude=30), kdims=['time'])
temp_map = xr_dataset.to(gv.Image,['longitude', 'latitude']) * gv.Points([(300,30)], crs=crs.PlateCarree())
temp_map + temp_curve

In [ ]:
%%output size=200
features = hv.Overlay([gf.land, gf.ocean, gf.rivers, gf.lakes, gf.borders, gf.coastline])
features

In [ ]:
projections = [crs.RotatedPole, crs.Mercator, crs.LambertCylindrical, crs.Geostationary, 
               crs.AzimuthalEquidistant, crs.OSGB, crs.EuroPP, crs.Gnomonic, crs.PlateCarree, 
               crs.Mollweide, crs.OSNI, crs.Miller, crs.InterruptedGoodeHomolosine,
               crs.LambertConformal, crs.SouthPolarStereo, crs.AlbersEqualArea, crs.Orthographic,
               crs.NorthPolarStereo, crs.Robinson]

In [ ]:
hv.Layout([gf.coastline.relabel(group=p.__name__)(plot=dict(projection=p()))
           for p in projections])

In [ ]:
%output size=200
(features.relabel(group='Mollweide')(plot=dict(projection=crs.Mollweide(central_longitude=160))) +
features.relabel(group='Geostationary')(plot=dict(projection=crs.Geostationary(central_longitude=-90))))

In [ ]:
%%opts Image [projection=crs.Geostationary(central_longitude=120)] (cmap='Greens') Overlay [xaxis=None yaxis=None]
xr_dataset.to.image(['longitude', 'latitude']) * gf.coastline * gf.borders

In [ ]:
%%opts Image [projection=crs.Geostationary()] (cmap='Greens') Overlay [xaxis=None yaxis=None]
max_surface_temp = xr_dataset.range('surface_temperature')[1]
print(max_surface_temp)
xr_dataset.redim(surface_temperature=dict(range=(300, max_surface_temp))).to(gv.Image,['longitude', 'latitude']) \
  * gf.coastline